In [2]:
from __future__ import print_function, division

from keras.datasets import mnist
from keras.layers import Input, Dense, Reshape, Flatten, Dropout, multiply, GlobalAveragePooling2D, MaxPooling2D
from keras.layers import BatchNormalization, Activation, Embedding, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Sequential, Model
from keras.optimizers import Adam

import matplotlib.pyplot as plt

import numpy as np
from scipy.misc import imread
from scipy.misc import imresize
from scipy.misc import imsave
import glob
import random

from keras.preprocessing.image import ImageDataGenerator
from keras import applications
from keras.optimizers import SGD
from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau
from keras.callbacks import EarlyStopping
from keras.utils import to_categorical
#from keras.applications.resnet50 import preprocess_input

from keras.applications.resnet50 import ResNet50
from keras.preprocessing import image
from keras.applications.resnet50 import preprocess_input, decode_predictions
#from keras.applications.vgg19 import preprocess_input as preprocess_vgg
from keras.applications.inception_v3 import preprocess_input as inception_preprocess

#from keras.applications.inception_resnet_v2 import preprocess_input

import numpy as np

import keras
import copy
import cv2

from keras.models import *
from keras.layers import *
from keras.optimizers import *

import numpy as np 
import os
import numpy as np
from keras.callbacks import ModelCheckpoint, LearningRateScheduler
from keras import backend as keras

Using TensorFlow backend.


In [3]:
path = '../data/'
savepath = '../data/'
images = glob.glob(path+'new_data/*.npy')

In [4]:
tile_sizes = np.loadtxt(path+'tile_sizes.txt', dtype='int')
tile_sizes = tile_sizes[:150]
images_sampled = {}
for tile in tile_sizes:
    for i in range(1, 31):
        images_sampled.setdefault(tile[0]*30+i, []).append(tile[1])

In [5]:
def myGenerator(batch_size):
    while True:
        index_list = random.sample(images_sampled.keys(), batch_size)
        alldata_x = []
        alldata_y = []
        for i in index_list:
            frame = path+'sources/nparrs_384/frame'+str(i)+'.npy'
            frame = np.load(frame)
            tile_index = random.choice(images_sampled[i])
            
            temp  = imresize(frame[tile_index], (24, 24))
            temp  = imresize(temp, (384, 384))
            
            alldata_x.append(temp)
            alldata_y.append(frame[tile_index])
        
        alldata_x = np.array(alldata_x)
        alldata_y = np.array(alldata_y)
        
        alldata_y = (alldata_y.astype(np.float32) - 127.5) / 127.5
        alldata_x = alldata_x.astype(np.float32)/255.0
        
        yield alldata_x, alldata_y

#x = myGenerator(10)
#xtrain, ytrain = next(x)
#print('xtrain shape:',xtrain.shape)
#print('ytrain shape:',ytrain.shape)

In [14]:
class CGAN():
    def __init__(self):
        # Input shape
        self.img_rows = 384
        self.img_cols = 384
        self.channels = 3
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.optimizer = Adam(0.0002, 0.5)

        # Build and compile the discriminator
        #self.discriminator = self.build_discriminator()
        #self.discriminator.compile(loss=['mse'],
        #    optimizer=optimizer,
        #    metrics=['accuracy'])
        
        #print(self.discriminator.summary())
        
        # Build the generator
        self.generator = self.build_generator()
        
        print(self.generator.summary())
        
        noise = Input(shape=(384, 384, 3))
        img = self.generator(noise)

        # For the combined model we will only train the generator
        #self.discriminator.trainable = False

        # The discriminator takes generated image as input and determines validity
        # and the label of that image
        #valid = self.discriminator(img)
        
        # The combined model  (stacked generator and discriminator)
        # Trains generator to fool discriminator
        #self.combined = Model(noise, [img, valid])
        #self.combined.compile(loss=['mse', 'mse'],
        #    loss_weights=[0.9, 0.1],
        #    optimizer=optimizer)

    def build_generator(self):
        input_size = (384,384,3)
        inputs = Input(input_size)


        conv1 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(inputs)
        conv1 = LeakyReLU()(conv1)
        conv1 = BatchNormalization(momentum=0.8)(conv1)



        conv2 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv1)
        conv2 = LeakyReLU()(conv2)
        conv2 = BatchNormalization(momentum=0.8)(conv2)

        conv3 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv2)
        conv3 = LeakyReLU()(conv3)
        conv3 = BatchNormalization(momentum=0.8)(conv3)

        concat1 = add([conv1, conv3])



        conv4 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(concat1)
        conv4 = LeakyReLU()(conv4)
        conv4 = BatchNormalization(momentum=0.8)(conv4)

        conv5 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv4)
        conv5 = LeakyReLU()(conv5)
        conv5 = BatchNormalization(momentum=0.8)(conv5)

        concat2 = add([conv5, concat1])



        conv6 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(concat2)
        conv6 = LeakyReLU()(conv6)
        conv6 = BatchNormalization(momentum=0.8)(conv6)

        conv7 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv6)
        conv7 = LeakyReLU()(conv7)
        conv7 = BatchNormalization(momentum=0.8)(conv7)

        concat3 = add([conv7, concat2])



        conv8 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(concat3)
        conv8 = LeakyReLU()(conv8)
        conv8 = BatchNormalization(momentum=0.8)(conv8)

        conv9 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv8)
        conv9 = LeakyReLU()(conv9)
        conv9 = BatchNormalization(momentum=0.8)(conv9)
        

        conv10 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv9)
        conv10 = LeakyReLU()(conv10)
        conv10 = BatchNormalization(momentum=0.8)(conv10)

        concat4 = add([conv10, conv1])
        
        conv11 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(concat4)
        conv11 = LeakyReLU()(conv11)
        conv11 = BatchNormalization(momentum=0.8)(conv11)
        
        conv12 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv11)
        conv12 = LeakyReLU()(conv12)
        conv12 = BatchNormalization(momentum=0.8)(conv12)


        out = Conv2D(3, 3, padding = 'same', kernel_initializer = 'he_normal')(conv12)
        out = LeakyReLU()(out)
        out = BatchNormalization(momentum=0.8)(out)


        model = Model(input = inputs, output = out)
        return model
    
    def build_autoencoder(self):
        self.generator.compile(loss=['mse'],optimizer=self.optimizer)
    
    def train_generator_autoencoder(self, epochs, batch_size=128, sample_interval=10):
        for epoch in range(epochs):
            X_train, y_train = next(myGenerator(batch_size))
            g_loss = self.generator.train_on_batch(X_train, y_train)
            print ("Epoch ", epoch, " G loss ", g_loss)
            if epoch % sample_interval == 0:
                self.sample_images(epoch)
                self.generator.save_weights(savepath+'weights/generator_weights_'+str(epoch)+'.h5')

    def sample_images(self, epoch):
        r, c             = 1, 10
        X_train, y_train = next(myGenerator(10))
        gen_imgs         = self.generator.predict(X_train)
        
        # Rescale images 0 - 1
        temp     = (0.5 * gen_imgs + 0.5)*255
        gen_imgs = temp.astype(int)
        y_train = (0.5 * y_train + 0.5)*255
        y_train = y_train.astype(int)
        X_train = X_train*255
        X_train = X_train.astype(int)
        
        combined = np.array([gen_imgs[0], gen_imgs[1], gen_imgs[2], gen_imgs[3], gen_imgs[4], gen_imgs[5], gen_imgs[6], gen_imgs[7], gen_imgs[8], gen_imgs[9]])
        combined = np.hstack(combined.reshape(10, 384,384, 3))
        imsave(savepath+"images/"+str(epoch)+".png", combined)
        
        combined = np.array([y_train[0], y_train[1], y_train[2], y_train[3], y_train[4], y_train[5], y_train[6], y_train[7], y_train[8], y_train[9]])
        combined = np.hstack(combined.reshape(10, 384,384, 3))
        imsave(savepath+"images/"+str(epoch)+"_real.png", combined)
        
        combined = np.array([X_train[0], X_train[1], X_train[2], X_train[3], X_train[4], X_train[5], X_train[6], X_train[7], X_train[8], X_train[9]])
        combined = np.hstack(combined.reshape(10, 384,384, 3))
        imsave(savepath+"images/"+str(epoch)+"_lowres.png", combined)

In [55]:
cgan = CGAN()
cgan.build_autoencoder()
cgan.train_generator_autoencoder(200000, 10, 100)

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:119: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("ba...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_21 (InputLayer)           (None, 384, 384, 3)  0                                            
__________________________________________________________________________________________________
conv2d_127 (Conv2D)             (None, 384, 384, 16) 448         input_21[0][0]                   
__________________________________________________________________________________________________
leaky_re_lu_113 (LeakyReLU)     (None, 384, 384, 16) 0           conv2d_127[0][0]                 
__________________________________________________________________________________________________
batch_normalization_127 (BatchN (None, 384, 384, 16) 64          leaky_re_lu_113[0][0]            
__________________________________________________________________________________________________
conv2d_128

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:12: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  if sys.path[0] == '':


Epoch  0  G loss  1.3565364


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:149: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:153: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:157: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.


...

Epoch  102631  G loss  0.016416566
Epoch  102632  G loss  0.013100149
Epoch  102633  G loss  0.06614603
Epoch  102634  G loss  0.021199292
Epoch  102635  G loss  0.13093178
Epoch  102636  G loss  0.08104453
Epoch  102637  G loss  0.017082887
Epoch  102638  G loss  0.035107393
Epoch  102639  G loss  0.01922272
Epoch  102640  G loss  0.015124485
Epoch  102641  G loss  0.020560017
Epoch  102642  G loss  0.021208003
Epoch  102643  G loss  0.024026275
Epoch  102644  G loss  0.042742163
Epoch  102645  G loss  0.031809695
Epoch  102646  G loss  0.016318643
Epoch  102647  G loss  0.06000954
Epoch  102648  G loss  0.02198341
Epoch  102649  G loss  0.0298419
Epoch  102650  G loss  0.021433802
Epoch  102651  G loss  0.014771722
Epoch  102652  G loss  0.018470963
Epoch  102653  G loss  0.017026858
Epoch  102654  G loss  0.15708447
Epoch  102655  G loss  0.041806534
Epoch  102656  G loss  0.13104606
Epoch  102657  G loss  0.09343739
Epoch  102658  G loss  0.020529944
Epoch  102659  G loss  0.049602

Epoch  102868  G loss  0.080843166
Epoch  102869  G loss  0.11672195
Epoch  102870  G loss  0.027919475
Epoch  102871  G loss  0.010236191
Epoch  102872  G loss  0.024859885
Epoch  102873  G loss  0.03827723
Epoch  102874  G loss  0.08233382
Epoch  102875  G loss  0.09281308
Epoch  102876  G loss  0.042882226
Epoch  102877  G loss  0.051024675
Epoch  102878  G loss  0.043972857
Epoch  102879  G loss  0.01730771
Epoch  102880  G loss  0.017475145
Epoch  102881  G loss  0.06526871
Epoch  102882  G loss  0.027499456
Epoch  102883  G loss  0.04145166
Epoch  102884  G loss  0.012842944
Epoch  102885  G loss  0.06510104
Epoch  102886  G loss  0.014132689
Epoch  102887  G loss  0.012283022
Epoch  102888  G loss  0.018815087
Epoch  102889  G loss  0.09592719
Epoch  102890  G loss  0.01912218
Epoch  102891  G loss  0.018955061
Epoch  102892  G loss  0.037054133
Epoch  102893  G loss  0.019278878
Epoch  102894  G loss  0.04482706
Epoch  102895  G loss  0.017457547
Epoch  102896  G loss  0.010849

Epoch  103105  G loss  0.06720611
Epoch  103106  G loss  0.109764576
Epoch  103107  G loss  0.017931493
Epoch  103108  G loss  0.010273861
Epoch  103109  G loss  0.03814156
Epoch  103110  G loss  0.013068123
Epoch  103111  G loss  0.018844303
Epoch  103112  G loss  0.021405546
Epoch  103113  G loss  0.0339622
Epoch  103114  G loss  0.021331286
Epoch  103115  G loss  0.04946967
Epoch  103116  G loss  0.05275604
Epoch  103117  G loss  0.03479498
Epoch  103118  G loss  0.16242513
Epoch  103119  G loss  0.017307367
Epoch  103120  G loss  0.056390513
Epoch  103121  G loss  0.029489601
Epoch  103122  G loss  0.031498495
Epoch  103123  G loss  0.01966648
Epoch  103124  G loss  0.065404646
Epoch  103125  G loss  0.009650877
Epoch  103126  G loss  0.0340347
Epoch  103127  G loss  0.014773317
Epoch  103128  G loss  0.024623837
Epoch  103129  G loss  0.14205678
Epoch  103130  G loss  0.01803484
Epoch  103131  G loss  0.0194675
Epoch  103132  G loss  0.067298695
Epoch  103133  G loss  0.03154499
E

Epoch  103342  G loss  0.02798586
Epoch  103343  G loss  0.020224234
Epoch  103344  G loss  0.1193048
Epoch  103345  G loss  0.017474905
Epoch  103346  G loss  0.051618524
Epoch  103347  G loss  0.04728555
Epoch  103348  G loss  0.1334196
Epoch  103349  G loss  0.026004147
Epoch  103350  G loss  0.027798008
Epoch  103351  G loss  0.013224015
Epoch  103352  G loss  0.14522083
Epoch  103353  G loss  0.020072456
Epoch  103354  G loss  0.020280752
Epoch  103355  G loss  0.015464313
Epoch  103356  G loss  0.02608034
Epoch  103357  G loss  0.030665472
Epoch  103358  G loss  0.016238304
Epoch  103359  G loss  0.030771816
Epoch  103360  G loss  0.010176837
Epoch  103361  G loss  0.11656724
Epoch  103362  G loss  0.026606608
Epoch  103363  G loss  0.07336788
Epoch  103364  G loss  0.04936701
Epoch  103365  G loss  0.050873242
Epoch  103366  G loss  0.09857361
Epoch  103367  G loss  0.101113394
Epoch  103368  G loss  0.19791469
Epoch  103369  G loss  0.03316418
Epoch  103370  G loss  0.026721936

KeyboardInterrupt: 

In [15]:
cgan2 = CGAN()
cgan2.generator.load_weights('../data/superresolution_48x48/PerSegment-FilterSize8/weights/generator_weights_100000.h5')

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:116: UserWarning: Update your `Model` call to the Keras 2 API: `Model(outputs=Tensor("ba..., inputs=Tensor("in...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_9 (InputLayer)            (None, 384, 384, 3)  0                                            
__________________________________________________________________________________________________
conv2d_55 (Conv2D)              (None, 384, 384, 8)  224         input_9[0][0]                    
__________________________________________________________________________________________________
leaky_re_lu_55 (LeakyReLU)      (None, 384, 384, 8)  0           conv2d_55[0][0]                  
__________________________________________________________________________________________________
batch_normalization_55 (BatchNo (None, 384, 384, 8)  32          leaky_re_lu_55[0][0]             
__________________________________________________________________________________________________
conv2d_56 

In [24]:
for i in range(1000):
    x = myGenerator(1)
    xtest, ytest = next(x)
    pred = cgan2.generator.predict(xtest)
    pred = pred*255
    pred = pred.astype(int)
    #plt.imshow(pred[0])
    #plt.show()
    ytest = ytest*127.5+127.5
    ytest = ytest.astype(int)
    #plt.imshow(ytest[0])
    #plt.show()
    imsave(path+'test/frame_pred'+str(i)+'.png', pred[0])
    imsave(path+'test/frame_real'+str(i)+'.png', ytest[0])

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:12: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  if sys.path[0] == '':
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:13: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
  del sys.path[0]
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:14: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
  


In [25]:
import numpy 
import math
import cv2

def psnr(img1, img2):
    mse = numpy.mean( (img1 - img2) ** 2 )
    if mse == 0:
        return 100
    PIXEL_MAX = 255.0
    return 20 * math.log10(PIXEL_MAX / math.sqrt(mse))

In [33]:
data = []
for i in range(1000):
    img1 = cv2.imread(path+'test/frame_real'+str(i)+'.png')
    img2 = cv2.imread(path+'test/frame_pred'+str(i)+'.png')
    d = psnr(img1, img2)
    data.append(d)
print('PSNR:', np.mean(data))

PSNR: 29.01294903355552
